<a href="https://colab.research.google.com/github/tluxxx/vbt_basics/blob/main/vbt_test_04.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Introduction into vectorbt - part 4
* valid for latest free version (version: 0.28.1)
* portfolio with one ticker

Content:
* "alternating" vs. "non-alternating" signals
* multiple order per trades and position accumulation
* stop losses for accumulated positions  
* ShortOnly strategies
* Long and Short strategies
* impact of `allow_partial`

In [ ]:
!pip install vectorbt ta python-dotenv --quiet

  Preparing metadata (setup.py) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 420.7/420.7 kB 9.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 315.5/315.5 kB 16.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.6/1.6 MB 24.8 MB/s eta 0:00:00


In [ ]:
import vectorbt as vbt
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import plotly.graph_objects as go
from plotly.subplots import make_subplots

import yfinance as yf
import ta

## 0. Helpers

In [ ]:
import sys
import importlib
import os
import helper

from google.colab import drive
from dotenv import load_dotenv

# connnecting Google-Drive, loading .env-file and getting path_data
from pathlib import Path
drive.mount('/content/drive')
load_dotenv('/content/drive/My Drive/.env')
path_data = os.getenv('PATH_VBT')               # replace it with your path
sys.path.append(path_data)

# importing supporting functions (from helper-module in path_data)
for mod in ['timelines', 'entries_exits', 'plotting_support']:
    importlib.reload(importlib.import_module(f'helper.{mod}'))

from helper.timelines import get_timeline_basic, get_timeline_extended
from helper.entries_exits import lense_at_entry_exit, classify_exit_types
from helper.plotting_support import (_is_boolean_series, plot_multi_subplot_trading_data,
                                     plot_signals_and_positions)


Mounted at /content/drive


In [ ]:
pd.set_option('display.float_format', '{:.2f}'.format)

## 1. Data-Download and Signal Generation

The data download is identical to the previous parts. Previously, we have used strategies based on "alternating" signals.

These are strategies where an entry signal is always followed by an exit signal, that in turn is followed by an entry signal again, and so on. Examples are SMA-crossing-strategies. Each cross-over (= entry signal) is followed by an cross-under (= exitsignal) etc... Other examples are MACD-crossing strategies.

Now we will implement strategies based on "non-alternating" signals. Here entry- and exits-signals are not in a strong alternating sequence. We may have in a timeline a multitude of entry signals without an exit signal in between  and vice versa.

We will use the following mean reverse-strategy (that is based on "non-alternating" signals). The strategy can be described as follows:

* We will calculate the Bollinger Bands using the parameters:
    * n = length of the window to calculate the mean(n) of the close and the Standard Deviation (std(n)) of the difference between close and mean(n).
    * nb = number of Standard-Deviations between mean and upper/lower Band;  BB_up/BB_low = mean(n) +- nb *std(n)
* Entry-signals of the strategy: Buy, if touching BB_low (i.e. close crosses under (or) over BB_low)
* Exit-signals of the strategy: Sell, if touching BB_up (i.e. close crosses over (or) under BB_up)








In [ ]:
# download data
ticker = 'AAPL'
start_date = '2022-01-01'
end_date = '2025-10-11'
prices = yf.download(ticker, start=start_date, end=end_date, auto_adjust=True)

# preparing for ta & vbt-use (remove MultiLevel-column-index, transform to a pd.Series)
close = prices.Close[ticker]
open = prices.Open[ticker]
high = prices.High[ticker]
low = prices.Low[ticker]

# mean-return-strategy using bollinger-bands
bb = ta.volatility.BollingerBands(close, window=20, window_dev=2)
bb_upper = bb.bollinger_hband()
bb_middle = bb.bollinger_mavg()
bb_lower = bb.bollinger_lband()
bb_width = bb.bollinger_wband()

# signal generation:
entry_1 = (close < bb_lower) & (close.shift(1) > bb_lower.shift(1))
entry_2 = (close > bb_lower) & (close.shift(1) < bb_lower.shift(1))
exit_1 = (close > bb_upper) & (close.shift(1) < bb_upper.shift(1))
exit_2 = (close < bb_upper) & (close.shift(1) > bb_upper.shift(1))

entries =  (entry_1  | entry_2).rename(ticker)   # entry at touching (= crossing (under or over)) of lower band
exits = (exit_1 | exit_2).rename(ticker)         # exit at touching (=crossing (under or over)) of upper band


[*********************100%***********************]  1 of 1 completed


## 2. Portfolio, based on "non-alternating" signals
We first define a baseline-portfolio for reference as follows:
* strategy based entries and exits
* trailing StopLoss
* TakeProfit-limit

In order to demonstrate the behaviour (in its 'purest' fashion), we have excluded fees, slippage, non-default prices (as at next-bar-at-open), size_types, size, etc..

In [ ]:
# stop parameter
stop_loss = 0.1             # 10%
stop_loss_trail = True      # trailing-stop-loss
take_profit = 0.15          # 15%

# generate a portfolio instance with all three types of exits
pf = vbt.Portfolio.from_signals(
    close,                      # price info (defines also the index of any timeline)
    entries,                    # series (boolean) of entry-signals
    exits,                      # series (boolean) of entry-signals
    sl_stop=stop_loss,          # stop loss
    sl_trail=stop_loss_trail,   # trailing stop loss
    tp_stop=take_profit,        # take profit
    init_cash=10_000,           # initial cash
    freq='D',                   # all parameters on daily base

)

First we will use our already introduced methods of tabulating the trades,  including an additional column `exit_type`, as described in the previous parts.

Next we will calculate out timeline-dataframe.

Using our function `get_timeline_extended` we will receive the OHLC-data, the (raw) entry/exit-signals and the columns with the effective entry and effective exits (True at open/closing a position, False otherwise). In addition we will get for each type of exit (by system, by StopLoss, by TakeProfit) a separate column with True if an exit signal at that time is effective (i.e. closes the position for the particular reason) False otherwise.

Finally we will add the indicator-values (here the Bollinger Bands) and some Portfolio-parameters for our inspection/analyses.



In [ ]:
# list of trades with key data, amended by the trade type
trades = classify_exit_types(
    trades=pf.trades.records_readable,
    take_profit=take_profit,
    exits=exits
)

# generating timeline for standard + specific trading parameter
timeline = get_timeline_extended(prices, entries, exits, trades)     # standards (price, entry, exits)
timeline['bb_upper'] = bb_upper
timeline['bb_lower'] = bb_lower
timeline['bb_middle'] = bb_middle

# portfolio
timeline['position'] = np.sign(pf.net_exposure())
timeline['pnl'] = pf.cumulative_returns()
timeline['assets'] = pf.assets()
timeline['cash'] = pf.cash()
timeline['value'] = pf.value()
timeline['gross_exposure'] = pf.gross_exposure()
timeline['net_exposure'] = pf.net_exposure()

In [ ]:
trades.head(3)

Exit Trade Id Column  Size Entry Timestamp  Avg Entry Price  Entry Fees  \
0              0   AAPL 65.90      2022-03-11           151.74        0.00   
1              1   AAPL 73.16      2022-04-26           153.77        0.00   
2              2   AAPL 72.86      2022-05-13           144.48        0.00   

  Exit Timestamp  Avg Exit Price  Exit Fees      PnL  Return Direction  \
0     2022-03-24          170.71       0.00  1249.92    0.12      Long   
1     2022-05-11          143.88       0.00  -723.55   -0.06      Long   
2     2022-06-13          129.52       0.00 -1089.78   -0.10      Long   

   Status  Position Id  exit_type  
0  Closed            0     system  
1  Closed            1  stop_loss  
2  Closed            2  stop_loss

In [ ]:
timeline.columns

Index(['open', 'high', 'low', 'close', 'sys_entries', 'sys_exits',
       'eff_entries', 'eff_exits_system', 'eff_exits_stop_loss',
       'eff_exits_take_profit', 'bb_upper', 'bb_lower', 'bb_middle',
       'position', 'pnl', 'assets', 'cash', 'value', 'gross_exposure',
       'net_exposure'],
      dtype='object')

In [ ]:
# plot configuration 01:
# 1. Subplot: Candlesticks, SMA's, effective Entry/Exit-Signals;
# 2. Subplot: PnL
# 3. Subplot: Positions

subplot_config_01 = [
    {"title": "Prices, Indicators, effective Signals", "height_ratio": 8,
     "traces": [
          {"type": "candlestick", "open": "open", "high": "high", "low": "low", "close": "close"},
          {"type": "scatter", "y": "bb_upper", "name": "upper BB", "line": {"color": "orange"}},
          {"type": "scatter", "y": "bb_lower", "name": "lower BB", "line": {"color": "yellow"}},
          {"type": "scatter", "y": "bb_middle", "name": "middle-BB", "line": {"color": "green"}},
          {"type": "scatter_markers", "y": "eff_entries", "marker": {"color": "green", "symbol": "triangle-up", "size": 15}},
          {"type": "scatter_markers", "y": "eff_exits_system", "marker": {"color": "red", "symbol": "triangle-down", "size": 15}},
          {"type": "scatter_markers", "y": "eff_exits_stop_loss", "marker": {"color": "blue", "symbol": "triangle-down", "size": 15}},
          {"type": "scatter_markers", "y": "eff_exits_take_profit", "marker": {"color": "grey", "symbol": "triangle-down", "size": 15}},
        ],
    },

    { "title": "PnL", "height_ratio": 3,
     "traces": [
         {"type": "scatter", "y": "pnl", "name": "PnL", "line": {"color": "salmon", "width": 2},
          "mode": "lines"
          }
         ],
    },

    { "title": "Position", "height_ratio": 1,
     "traces": [
         {"type": "scatter", "y": "position", "name": "Position", "line": {"color": "green", "width": 2},
          "line_shape": "hv",
          "mode": "lines"
          }
         ],
    },
]

We observe a multitude of entries, followed by different types of exits (system, stop-loss and take-profit)

In [ ]:
fig = plot_multi_subplot_trading_data(
    timeline,
    subplot_config_01,
    title = f'Overview for {ticker}, from {start_date} to {end_date}',
    size=(1400, 500),
    theme='plotly',
)
fig.show()


For better visualisation, we slice the timeline-dataframe to an interval of interest and use our general plotting function  `plot_multi_subplot_trading_data`.

In [ ]:
# focusing on an intervall for analyses
start_analyses='2022-03-01'
end_analyses='2023-01-31'
timeline_slice = timeline.loc[start_analyses:end_analyses]

In [ ]:
fig = plot_multi_subplot_trading_data(
    timeline_slice,
    subplot_config_01,
    title = f'slice for {ticker}, from {start_analyses} to {end_analyses}',
    size=(1400, 500),
    theme='plotly',
)
fig.show()

Now we take a deeper dive into "non-alternating"-signals.

We plot the following parameters:
* (raw = original) entry and exit signals (entry = +1 in green, exit = -1 in red) as generated by our strategy
* effective entries and exits as calculated by `Portfolio` (together with an marker, describing the type, that triggered the relavent exit)
* effective position (as returned from Portfolio-instance)
* number of assets (as returned from Portfolio-instance)

We can clearly observe a difference between (raw) entry/exit-signals and effective entries/exits.

The `Portfolio`-instance does the following job for us:
* entry signals at a certain bar are **executed only**  if we are **not in a position**, otherwise entry signals will be ingnored.
* exit signals at a certain bar are **executed only**, if we are **in a position**, otherwise exit-signals will be ignored.

When executing a entry-signal, it is assumed (default setting of `size_type` and `size`) that all available cash is used, therefore if a second entry-trade signal occurs, there is simply no cash anymore to execute an order, the signal is ignored. So we can differentiate between raw and the executed (= **effective**) entry signals.  

Same is with exits signals. Out of the multitude of exit signals only these are execuded when still in position. We can differentiate between raw and the executed (= **effective**) exit signals. For effective exit signals, we can also define the type.  

So from a "wild" mixture of (non-alternating) raw entry and exit signals the `Portfolio`-instance will generate a clear in/out-position timeline (and effective entry and exit-signals), by ignoring non relevant signals regardless how many raw entry/exit signals are provided.

To visualize this, we have generated the function `plot_signals_and_positions`. The function provides as dashboard, visualizing the original signals, the effective signals (that are a subpart of it), tha trade type (differentiating between exits, triggered by the Strategy, StopLoss or TakeProfit). We also plot the timelines of the number of assets hold and the cash.  

In [ ]:
# plotting details
title = f'Comparison of System Signals, Effective Signals, Position, Assets and Cash for {ticker}'
plot_signals_and_positions(trades, timeline, entries, exits, ticker, title)

#' 3. The impact of `accumulate` on `Portfolio`

We keep all parameters as above, but change the following parameters:
* we switch `accumulate` to True.
* we explicitely set `size_type`to 'Percent'
* we set `size`to 0.3.

As mentioned in the previous parts, the settings of `size_type`and `size` will enforce, that we use 30% of the available cash for each trade.

Now lets study the impact of `accumulate`. We ill generate a portfolio as follows:  

In [ ]:
# stop parameter
stop_loss = 0.1             # 10%
stop_loss_trail = True      # trailing-stop-loss
take_profit = 0.15          # 15%

# generate a portfolio instance with all three types of exits
pf = vbt.Portfolio.from_signals(
    close,                      # price info (defines also the index of any timeline)
    entries,                    # series (boolean) of entry-signals
    exits,                      # series (boolean) of entry-signals
    sl_stop=stop_loss,          # stop loss at 5%
    sl_trail=stop_loss_trail,   # trailing stop loss
    tp_stop=take_profit,        # take profit at 15%
    size_type='Percent',        # percent available cash
    size=0.3,                   # 30%
    accumulate=True,            # accumulate position
    init_cash=10_000,           # initial cash
    freq='D',                   # all parameters on daily base
)

In [ ]:
# list of trades with key data, amended by the trade type
trades = classify_exit_types(
    trades=pf.trades.records_readable,
    take_profit=take_profit,
    exits=exits
)

# generating timeline for standard + specific trading parameter
timeline=get_timeline_extended(prices, entries, exits, trades)     # standards (price, entry, exits)
timeline['bb_upper'] = bb_upper
timeline['bb_lower'] = bb_lower
timeline['bb_middle'] = bb_middle
timeline['position'] = np.sign(pf.net_exposure())

timeline['cash'] = pf.cash()
timeline['cash_flow'] = pf.cash_flow()
timeline['assets'] = pf.assets()
timeline['asset_flow'] = pf.asset_flow()
timeline['asset_value'] = pf.asset_value()
timeline['value'] = pf.value()

timeline['gross_exposure'] = pf.gross_exposure()
timeline['net_exposure'] = pf.net_exposure()

timeline['pnl'] = pf.cumulative_returns()

In [ ]:
fig = plot_multi_subplot_trading_data(
    timeline,
    subplot_config_01,
    title = f'Overview for {ticker}, from {start_date} to {end_date}',
    size=(1400, 500),
    theme='plotly',
)
fig.show()

We now observe completely different behavior.

Entry Signals
* An entry signal is executed as long as cash is available. Since we invest only 30% of available cash, there is always remaining cash for additional entries.
* Multiple entry signals therefore accumulate and gradually scale up the position size. (We will later show how to modify this behavior using `min_size` or `max_size` to enforce an intervall of order sizes.)

Exit Signals
* Strategy exits reduce the position but do not close it entirely: `size` = 0.3 means for each strategy-generated exit: sell 30% of the assets currently held (!!). Each strategy generated exit creates only a partial exit trade.
* StopLoss and TakeProfit exits behave differently: They always close the entire remaining position in one transaction.

This demonstrates how `accumulate`, `size_type`, and `size` fundamentally alter portfolio dynamics.

In [ ]:
#plotting details
title = f'Comparison of System Signals, Effective Signals, Position, Assets and Cash for {ticker}'
plot_signals_and_positions(trades, timeline, entries, exits, ticker, title)

For our current portfolio (with accumulation), the trade table becomes less intuitive and requires some explanation. Key point: one Position ID can contain multiple Exit Trade IDs.

Example: First Position
* Position ID = 0 contains Exit Trade IDs 0, 1.
* These correspond exactly to the two exit events seen on the timeline:
    * one strategy-driven partial exits,
    * followed by a TakeProfit that closes the remaining position.
* Size shows how many assets were sold at each exit:
    * first row = partial reduction,
    * second row = complete closure.
* Entry Timestamp = timestamp of the first entry signal of the position (identical for every entry (!!)).
* Avg Entry Price = volume-weighted average of all actual entry orders.

This may look inconsistent at first: entries data are "averaged" and are no longer deductible from timeline, however, exits are shown individually.

But this reflects:
* number of entries may differ from the number of exits,
* only exits are the definitive trade events used to compute PnL, so vbt lists each exit explicitly.

With Second and Third Position (Position ID = 1, 2) , we see similar behaviour:
* multiple entry signals
* multiple system-triggered exits
* final StopLoss or TakeProfit
* exits: date and prices as with effective signals
* entries:
    * date: date of first entry,
    * Avg Entry Price = volume-weighed price of all actual entry orders.

With Forth Position (Position ID = 3), we see a different behaviour:
* Built via multiple entries, but ends with one single StopLoss exit.
* Trade table shows one row only because there is only one exit event.
* Size = full asset size of the final position (closed at once).
* Entry Timestamp = first entry date of that position (the fact, that we have multiple entries is not shown in this example).
* Avg Entry Price = volume-weighted average of all entry order prices. position, the `Avg Entry Price` is the weighed average of all entry prices.
* Exit Timestamp = Date of the StopLoss-event
* Avg Exit Price = triggered StopLoss  






In [ ]:
trades.head(12)


Exit Trade Id Column  Size Entry Timestamp  Avg Entry Price  Entry Fees  \
0               0   AAPL 10.07      2022-03-11           151.89        0.00   
1               1   AAPL  7.05      2022-03-11           151.89        0.00   
2               2   AAPL 16.45      2022-03-11           151.89        0.00   
3               3   AAPL 67.24      2022-04-26           150.18        0.00   
4               4   AAPL 21.46      2022-06-14           130.39        0.00   
5               5   AAPL 31.91      2022-08-30           155.90        0.00   
6               6   AAPL  5.94      2022-10-03           140.10        0.00   
7               7   AAPL  4.16      2022-10-03           140.10        0.00   
8               8   AAPL  2.91      2022-10-03           140.10        0.00   
9               9   AAPL  2.04      2022-10-03           140.10        0.00   
10             10   AAPL  4.76      2022-10-03           140.10        0.00   
11             11   AAPL 10.81      2022-12-15           132.74        0.00   

   Exit Timestamp  Avg Exit Price  Exit Fees      PnL  Return Direction  \
0      2022-03-24          170.71       0.00   189.59    0.12      Long   
1      2022-03-25          171.35       0.00   137.21    0.13      Long   
2      2022-03-29          175.51       0.00   388.57    0.16      Long   
3      2022-06-13          129.52       0.00 -1388.52   -0.14      Long   
4      2022-07-20          150.31       0.00   427.42    0.15      Long   
5      2022-09-29          140.13       0.00  -503.30   -0.10      Long   
6      2022-10-25          149.83       0.00    57.80    0.07      Long   
7      2022-10-26          146.89       0.00    28.23    0.05      Long   
8      2022-10-28          153.17       0.00    38.06    0.09      Long   
9      2022-10-31          150.81       0.00    21.83    0.08      Long   
10     2022-11-03          136.59       0.00   -16.70   -0.03      Long   
11     2023-01-23          139.01       0.00    67.86    0.05      Long   

    Status  Position Id    exit_type  
0   Closed            0       system  
1   Closed            0       system  
2   Closed            0  take_profit  
3   Closed            1    stop_loss  
4   Closed            2  take_profit  
5   Closed            3    stop_loss  
6   Closed            4       system  
7   Closed            4       system  
8   Closed            4       system  
9   Closed            4       system  
10  Closed            4    stop_loss  
11  Closed            5       system

In [ ]:
# lense for inspecting timeline around entry/exit of first trade
entry_date = '2022-03-11'
exit_date = '2022-03-29'
lense_at_entry_exit(timeline, entry_date, exit_date, 1)


### Timeline around Entry Date: 2022-03-11 (1 rows before and after)



open   high    low  close  sys_entries  sys_exits  eff_entries  \
Date                                                                          
2022-03-10 157.11 157.29 152.97 155.46        False      False        False   
2022-03-11 155.86 156.21 151.52 151.74         True      False         True   
2022-03-14 148.53 151.15 147.20 147.71        False      False        False   

            eff_exits_system  eff_exits_stop_loss  eff_exits_take_profit  ...  \
Date                                                                      ...   
2022-03-10             False                False                  False  ...   
2022-03-11             False                False                  False  ...   
2022-03-14             False                False                  False  ...   

            position     cash  cash_flow  assets  asset_flow  asset_value  \
Date                                                                        
2022-03-10      0.00 10000.00       0.00    0.00        0.00         0.00   
2022-03-11      1.00  7000.00   -3000.00   19.77       19.77      3000.00   
2022-03-14      1.00  7000.00       0.00   19.77        0.00      2920.31   

              value  gross_exposure  net_exposure   pnl  
Date                                                     
2022-03-10 10000.00            0.00          0.00  0.00  
2022-03-11 10000.00            0.30          0.30  0.00  
2022-03-14  9920.31            0.29          0.29 -0.01  

[3 rows x 23 columns]



### Timeline around Exit Date: 2022-03-29 (1 rows before and after)



open   high    low  close  sys_entries  sys_exits  eff_entries  \
Date                                                                          
2022-03-28 168.85 172.34 168.68 172.21        False      False        False   
2022-03-29 173.28 175.56 172.94 175.51        False      False        False   
2022-03-30 175.10 176.14 173.29 174.34        False      False        False   

            eff_exits_system  eff_exits_stop_loss  eff_exits_take_profit  ...  \
Date                                                                      ...   
2022-03-28             False                False                  False  ...   
2022-03-29             False                False                   True  ...   
2022-03-30             False                False                  False  ...   

            position     cash  cash_flow  assets  asset_flow  asset_value  \
Date                                                                        
2022-03-28      1.00  7827.80       0.00   16.45        0.00      2833.36   
2022-03-29      0.00 10715.37    2887.57    0.00      -16.45         0.00   
2022-03-30      0.00 10715.37       0.00    0.00        0.00         0.00   

              value  gross_exposure  net_exposure  pnl  
Date                                                    
2022-03-28 10661.16            0.27          0.27 0.07  
2022-03-29 10715.37            0.00          0.00 0.07  
2022-03-30 10715.37            0.00          0.00 0.07  

[3 rows x 23 columns]

In [ ]:
# lense for inspecting timeline around entry/exit of second trade
entry_date = '2022-08-30'
exit_date = '2022-09-29'
lense_at_entry_exit(timeline, entry_date, exit_date, 1)

### Timeline around Entry Date: 2022-08-30 (1 rows before and after)



open   high    low  close  sys_entries  sys_exits  eff_entries  \
Date                                                                          
2022-08-29 158.49 160.21 157.18 158.72        False      False        False   
2022-08-30 159.46 159.88 155.12 156.29         True      False         True   
2022-08-31 157.67 157.93 154.55 154.63        False      False        False   

            eff_exits_system  eff_exits_stop_loss  eff_exits_take_profit  ...  \
Date                                                                      ...   
2022-08-29             False                False                  False  ...   
2022-08-30             False                False                  False  ...   
2022-08-31             False                False                  False  ...   

            position    cash  cash_flow  assets  asset_flow  asset_value  \
Date                                                                       
2022-08-29      0.00 9754.27       0.00    0.00        0.00         0.00   
2022-08-30      1.00 6827.99   -2926.28   18.72       18.72      2926.28   
2022-08-31      1.00 6827.99       0.00   18.72        0.00      2895.16   

             value  gross_exposure  net_exposure   pnl  
Date                                                    
2022-08-29 9754.27            0.00          0.00 -0.02  
2022-08-30 9754.27            0.30          0.30 -0.02  
2022-08-31 9723.15            0.30          0.30 -0.03  

[3 rows x 23 columns]



### Timeline around Exit Date: 2022-09-29 (1 rows before and after)



open   high    low  close  sys_entries  sys_exits  eff_entries  \
Date                                                                          
2022-09-28 145.20 148.16 142.45 147.37        False      False        False   
2022-09-29 143.69 144.30 138.36 140.13         True      False        False   
2022-09-30 138.95 140.74 135.72 135.92        False      False        False   

            eff_exits_system  eff_exits_stop_loss  eff_exits_take_profit  ...  \
Date                                                                      ...   
2022-09-28             False                False                  False  ...   
2022-09-29             False                 True                  False  ...   
2022-09-30             False                False                  False  ...   

            position    cash  cash_flow  assets  asset_flow  asset_value  \
Date                                                                       
2022-09-28      1.00 4779.59       0.00   31.91        0.00      4702.36   
2022-09-29      0.00 9250.98    4471.38    0.00      -31.91         0.00   
2022-09-30      0.00 9250.98       0.00    0.00        0.00         0.00   

             value  gross_exposure  net_exposure   pnl  
Date                                                    
2022-09-28 9481.95            0.50          0.50 -0.05  
2022-09-29 9250.98            0.00          0.00 -0.07  
2022-09-30 9250.98            0.00          0.00 -0.07  

[3 rows x 23 columns]

## 4. Portfolio for ShortOnly Strategies
We now extend our mean-reversion setup to include both long and short signals. To keep the logic simple, we define the following rules:

Long Logic
* Entry-Long: when price touches (crosses under/over) the lower Bollinger Band.
* Exit-Long: when price crosses above the middle Bollinger Band.

Short Logic
* Entry-Short: when price touches (crosses under/over) the upper Bollinger Band.
* Exit-Short: when price crosses below the middle Bollinger Band.

NOTE: This is not a smart or profitable strategy, since trades are exited as soon as price returns to the middle Bollinger Band. The approach is intentionally simplistic and serves purely for demonstration purposes.

In [ ]:
# download data
ticker = 'AAPL'
start_date = '2022-01-01'
end_date = '2025-10-11'
prices = yf.download(ticker, start=start_date, end=end_date, auto_adjust=True)

# preparing for ta & vbt-use (remove MultiLevel-column-index, transform to a pd.Series
close = prices.Close[ticker]
open = prices.Open[ticker]
high = prices.High[ticker]
low = prices.Low[ticker]

# mean-reverse-strategy using bollinger-bands
bb = ta.volatility.BollingerBands(close, window=20, window_dev=2)
bb_upper = bb.bollinger_hband()
bb_middle = bb.bollinger_mavg()
bb_lower = bb.bollinger_lband()
bb_width = bb.bollinger_wband()

# signal generation:
entry_1 = (close < bb_lower) & (close.shift(1) > bb_lower.shift(1))
entry_2 = (close > bb_lower) & (close.shift(1) < bb_lower.shift(1))
exit_1 = (close > bb_middle) & (close.shift(1) < bb_middle.shift(1))

entry_3 = (close < bb_upper) & (close.shift(1) > bb_upper.shift(1))
entry_4 = (close > bb_upper) & (close.shift(1) < bb_upper.shift(1))
exit_2 = (close < bb_middle) & (close.shift(1) > bb_middle.shift(1))

entries =  (entry_1 | entry_2).rename(ticker)   # LONG-entry at touching (crossing under or over) of lower band
exits = exit_1.rename(ticker)                   # LONG-Exit at crossing over mid band

short_entries = (entry_3 | entry_4).rename(ticker)   # SHORT-entry at touching (crossing under or over) of upper band
short_exits = exit_2.rename(ticker)                  # SHORT-Exit at crossing under mid band


[*********************100%***********************]  1 of 1 completed


When generating our next portfolio instance, we will exclusively use the short-entry and short-exit signals. In other words, we are now implementing a ShortOnly strategy.

In [ ]:
# stop parameter
stop_loss = 0.1             # 10%
stop_loss_trail = True      # trailing-stop-loss
take_profit = 0.15          # 15%

# generate a portfolio instance for Short Trading s
pf = vbt.Portfolio.from_signals(
    close,                          # price info (defines also the index of any timeline)
    # entries,                      # no long entries
    # exits,                        # no long exits
    short_entries = short_entries,  # series (boolean) of SHORT-entry-signals
    short_exits = short_exits,      # series (boolean) of SHORT-entry-signals
    sl_stop=stop_loss,              # stop loss
    sl_trail=stop_loss_trail,       # trailing stop loss
    tp_stop=take_profit,            # take profit
    init_cash=10_000,               # initial cash
    freq='D',                       # all parameters on daily base
)

In [ ]:
# list of trades with key data, amended by the trade type
trades = classify_exit_types(
    trades=pf.trades.records_readable,
    take_profit=take_profit,
    exits=exits
)

# generating timeline for standard + specific trading parameter
timeline=get_timeline_extended(prices, entries, exits, trades)     # standards (price, entry, exits)
timeline['bb_upper'] = bb_upper
timeline['bb_lower'] = bb_lower
timeline['bb_middle'] = bb_middle

# portfolio
timeline['position'] = np.sign(pf.net_exposure())
timeline['pnl'] = pf.cumulative_returns()
timeline['assets'] = pf.assets()
timeline['cash'] = pf.cash()
timeline['value'] = pf.value()
timeline['gross_exposure'] = pf.gross_exposure()
timeline['net_exposure'] = pf.net_exposure()

We clearly see: if we are short, the parameter position (=`np.sign(pf.net_exposure())`) equals -1.

In [ ]:
fig = plot_multi_subplot_trading_data(
    timeline,
    subplot_config_01,
    title = f'Overview for {ticker}, from {start_date} to {end_date}',
    size=(1400, 500),
    theme='plotly',
)
fig.show()

In [ ]:
# Combine trades, PnL, exposure, and underwater plots (using built-in subplots)
fig = pf.plots(subplots=['trades','trade_pnl','net_exposure', 'underwater'],
               make_subplots_kwargs={'row_heights': [0.7, 0.1, 0.1, 0.1]},
               width=1400, height=600)
fig.show()

In [ ]:
pf.trades.records_readable.head(3)

Exit Trade Id Column  Size Entry Timestamp  Avg Entry Price  Entry Fees  \
0              0   AAPL 58.58      2022-03-24           170.71        0.00   
1              1   AAPL 68.67      2022-07-21           152.58        0.00   
2              2   AAPL 63.57      2022-10-25           149.83        0.00   

  Exit Timestamp  Avg Exit Price  Exit Fees     PnL  Return Direction  Status  \
0     2022-04-11          162.55       0.00  477.97    0.05     Short  Closed   
1     2022-08-10          166.45       0.00 -952.70   -0.09     Short  Closed   
2     2022-11-02          142.64       0.00  457.07    0.05     Short  Closed   

   Position Id  
0            0  
1            1  
2            2

Using our timeline and the `lens_at_entry_exits()` function, we can track the behavior of a ShortOnly strategy:

Short Entry
* Short-entry signal occurs at bar [i].
* Entry price: close [i]
* Assets: assets [i] = - value [i] / price [i] (negative indicates short position)
* Cash: cash [i] = cash [i-1] - assets [i] * price [i]

This simulates short-selling: assets are borrowed and sold, and the proceeds are available for further operations. By default, the value of shorted assets equals the available cash before the trade (somehow similar to fully investing cash in LongOnly strategies).

Position Updates (while in position)
* Cash and assets remain constant.
* Position value: value [i] = value [i-1] + assets [i] * (price [i-1] - price [i])

Short Exit
* Short-exit signal occurs at bar [j].
* Exit price: close [j]
* Assets: assets [j] = 0 (position fully closed)
* Cash: reduced by assets [j-1] * close [j]
* Value: value [j] = cash [j]

If Not in Position
* All parameters remain unchanged.

This can be observed, when looking at the first trade:

In [ ]:
# timeline around entry and exit of the first trade
entry_date = '2022-03-24'
exit_date = '2022-04-11'
n_r = 1             # number of rows before/aftr entry/exit
lense_at_entry_exit(timeline, entry_date, exit_date, n_r)

### Timeline around Entry Date: 2022-03-24 (1 rows before and after)



open   high    low  close  sys_entries  sys_exits  eff_entries  \
Date                                                                          
2022-03-23 164.75 169.31 164.41 166.93        False      False        False   
2022-03-24 167.76 170.78 166.93 170.71        False      False         True   
2022-03-25 170.52 171.90 169.42 171.35        False      False        False   

            eff_exits_system  eff_exits_stop_loss  eff_exits_take_profit  \
Date                                                                       
2022-03-23             False                False                  False   
2022-03-24             False                False                  False   
2022-03-25             False                False                  False   

            bb_upper  bb_lower  bb_middle  position   pnl  assets     cash  \
Date                                                                         
2022-03-23    168.32    149.34     158.83      0.00  0.00    0.00 10000.00   
2022-03-24    170.20    148.57     159.39     -1.00  0.00  -58.58 20000.00   
2022-03-25    171.85    147.89     159.87     -1.00 -0.00  -58.58 20000.00   

              value  gross_exposure  net_exposure  
Date                                               
2022-03-23 10000.00            0.00          0.00  
2022-03-24 10000.00            1.00         -1.00  
2022-03-25  9962.66            1.00         -1.00



### Timeline around Exit Date: 2022-04-11 (1 rows before and after)



open   high    low  close  sys_entries  sys_exits  eff_entries  \
Date                                                                          
2022-04-08 168.46 168.46 165.93 166.81        False      False        False   
2022-04-11 165.45 165.77 162.31 162.55        False      False        False   
2022-04-12 164.78 166.59 163.42 164.42        False      False        False   

            eff_exits_system  eff_exits_stop_loss  eff_exits_take_profit  \
Date                                                                       
2022-04-08             False                False                  False   
2022-04-11             False                 True                  False   
2022-04-12             False                False                  False   

            bb_upper  bb_lower  bb_middle  position  pnl  assets     cash  \
Date                                                                        
2022-04-08    181.55    151.10     166.32     -1.00 0.02  -58.58 20000.00   
2022-04-11    179.84    154.29     167.06      0.00 0.05    0.00 10477.97   
2022-04-12    178.56    156.80     167.68      0.00 0.05    0.00 10477.97   

              value  gross_exposure  net_exposure  
Date                                               
2022-04-08 10228.64            1.00         -1.00  
2022-04-11 10477.97            0.00          0.00  
2022-04-12 10477.97            0.00          0.00

In the second trade, we see the same behaviour:
* If a short-entry-signal is triggered, a number of assets is sold short (corresponding to the current portfolio-value), the incoming cash-flow is added to cash.
* If in position, cash and number of asset remains, portfolio.value is adapted.
* Once an effective short-exit-signal is triggered, the "sold" number of shares are "bought back" from the cash (as result, the cash is reduced).    

In [ ]:
# timeline around entry and exit of the second trade
entry_date = '2022-07-21'
exit_date = '2022-08-10'
n_r = 1             # number of rows before/aftr entry/exit
lense_at_entry_exit(timeline, entry_date, exit_date, n_r)

### Timeline around Entry Date: 2022-07-21 (1 rows before and after)



open   high    low  close  sys_entries  sys_exits  eff_entries  \
Date                                                                          
2022-07-20 148.42 150.97 147.68 150.31        False      False        False   
2022-07-21 151.74 152.79 149.23 152.58        False      False         True   
2022-07-22 152.62 153.49 150.67 151.34        False      False        False   

            eff_exits_system  eff_exits_stop_loss  eff_exits_take_profit  \
Date                                                                       
2022-07-20             False                False                  False   
2022-07-21             False                False                  False   
2022-07-22             False                False                  False   

            bb_upper  bb_lower  bb_middle  position  pnl  assets     cash  \
Date                                                                        
2022-07-20    150.78    131.39     141.09      0.00 0.05    0.00 10477.97   
2022-07-21    152.23    131.91     142.07     -1.00 0.05  -68.67 20955.94   
2022-07-22    153.34    132.36     142.85     -1.00 0.06  -68.67 20955.94   

              value  gross_exposure  net_exposure  
Date                                               
2022-07-20 10477.97            0.00          0.00  
2022-07-21 10477.97            1.00         -1.00  
2022-07-22 10562.96            1.00         -1.00



### Timeline around Exit Date: 2022-08-10 (1 rows before and after)



open   high    low  close  sys_entries  sys_exits  eff_entries  \
Date                                                                          
2022-08-09 161.31 163.09 160.56 162.20        False      False        False   
2022-08-10 164.91 166.55 164.15 166.45        False      False        False   
2022-08-11 167.26 168.17 165.42 165.71        False      False        False   

            eff_exits_system  eff_exits_stop_loss  eff_exits_take_profit  \
Date                                                                       
2022-08-09             False                False                  False   
2022-08-10             False                 True                  False   
2022-08-11             False                False                  False   

            bb_upper  bb_lower  bb_middle  position   pnl  assets     cash  \
Date                                                                         
2022-08-09    167.02    140.90     153.96     -1.00 -0.02  -68.67 20955.94   
2022-08-10    168.24    142.03     155.14      0.00 -0.05    0.00  9525.27   
2022-08-11    169.28    142.99     156.13      0.00 -0.05    0.00  9525.27   

             value  gross_exposure  net_exposure  
Date                                              
2022-08-09 9817.05            1.00         -1.00  
2022-08-10 9525.27            0.00          0.00  
2022-08-11 9525.27            0.00          0.00

For short trades, we can also use the parameters `size_type` and `size` to control the trading behaviour. In the portfolio-instance below, we short-sell only 30% of the portfolio value, once a short entry signal is triggered.   

In [ ]:
# stop parameter
stop_loss = 0.1             # 10%
stop_loss_trail = True      # trailing-stop-loss
take_profit = 0.15          # 15%

# generate a portfolio instance with all three types of exits
pf = vbt.Portfolio.from_signals(
    close,                          # price info (defines also the index of any timeline)
    # entries,                      # No Long Entry Signals,  series (boolean) of LONG-entry-signals
    # exits,                        # No Long Exit Signals series (boolean) of LONG entry-signals
    short_entries = short_entries,  # series (boolean) of SHORT-entry-signals
    short_exits = short_exits,      # series (boolean) of SHORT-entry-signals
    sl_stop=stop_loss,              # stop loss
    sl_trail=stop_loss_trail,       # trailing stop loss
    tp_stop=take_profit,            # take profit
    size_type='Percent',            # using % of value
    size = 0.3,                     # % of available cash used
    init_cash=10_000,               # initial cash
    freq='D',                       # all parameters on daily base
)

Compared to the previous case, we see much smaller postions as a consequence of not using the full value of the portfolio for short-selling.  As in Long-Trades, you can set `size_type` to 'Value' (where the trade-volume is  `size`-money-units) or you set `size_type` to 'Assets' (where the trade-volume is `size`-number of assets)

In [ ]:
pf.trades.records_readable.head(6)

Exit Trade Id Column  Size Entry Timestamp  Avg Entry Price  Entry Fees  \
0              0   AAPL 17.57      2022-03-24           170.71        0.00   
1              1   AAPL 19.94      2022-07-21           152.58        0.00   
2              2   AAPL 19.76      2022-10-25           149.83        0.00   
3              3   AAPL 21.60      2023-01-23           139.01        0.00   
4              4   AAPL 18.74      2023-03-20           155.30        0.00   
5              5   AAPL 17.29      2023-04-28           167.41        0.00   

  Exit Timestamp  Avg Exit Price  Exit Fees     PnL  Return Direction  Status  \
0     2022-04-11          162.55       0.00  143.39    0.05     Short  Closed   
1     2022-08-10          166.45       0.00 -276.68   -0.09     Short  Closed   
2     2022-11-02          142.64       0.00  142.04    0.05     Short  Closed   
3     2023-02-15          153.26       0.00 -307.63   -0.10     Short  Closed   
4     2023-04-12          157.96       0.00  -49.92   -0.02     Short  Closed   
5     2023-06-12          181.59       0.00 -245.11   -0.08     Short  Closed   

   Position Id  
0            0  
1            1  
2            2  
3            3  
4            4  
5            5

As with LongOnly-portfolios, we can also limit the size of an order by setting the parameter `min_size` to a nonzero value.

Note: regardless of the selected `size_type`; `min_size` and `max_size` are always expressed in number of assets. See the example below:

In [ ]:
# stop parameter
stop_loss = 0.1             # 10%
stop_loss_trail = True      # trailing-stop-loss
take_profit = 0.15          # 15%

# generate a portfolio instance with all three types of exits
pf = vbt.Portfolio.from_signals(
    close,                          # price info (defines also the index of any timeline)
    # entries,                      # No Long Entry Signals,  series (boolean) of LONG-entry-signals
    # exits,                        # No Long Exit Signals series (boolean) of LONG entry-signals
    short_entries = short_entries,  # series (boolean) of SHORT-entry-signals
    short_exits = short_exits,      # series (boolean) of SHORT-entry-signals
    sl_stop=stop_loss,              # stop loss
    sl_trail=stop_loss_trail,       # trailing stop loss
    tp_stop=take_profit,            # take profit
    size_type='Percent',            # using % of value
    size=0.3,                       # % of availalbe cash
    min_size=18,                    # min size in nb of assets per order
    max_size=20,                    # max_size in nb of assets per order
    init_cash=10_000,               # initial cash
    freq='D',                       # all parameters on daily base
)

Each order of size < `min_size` is ignored, number of assets per order is cut of at `max_size`, compared to the previous version.

In [ ]:
pf.trades.records_readable.head(6)

Exit Trade Id Column  Size Entry Timestamp  Avg Entry Price  Entry Fees  \
0              0   AAPL 19.66      2022-07-21           152.58        0.00   
1              1   AAPL 19.48      2022-10-25           149.83        0.00   
2              2   AAPL 20.00      2023-01-23           139.01        0.00   
3              3   AAPL 18.51      2023-03-20           155.30        0.00   

  Exit Timestamp  Avg Exit Price  Exit Fees     PnL  Return Direction  Status  \
0     2022-08-10          166.45       0.00 -272.77   -0.09     Short  Closed   
1     2022-11-02          142.64       0.00  140.03    0.05     Short  Closed   
2     2023-02-15          153.26       0.00 -284.85   -0.10     Short  Closed   
3     2023-04-12          157.96       0.00  -49.31   -0.02     Short  Closed   

   Position Id  
0            0  
1            1  
2            2  
3            3

## 5. LONG and SHORT Trades

Now we implement the full mean reversal strategy, allowing both Long and Short Positions.

An instance of the portfolio class is generated as follows:  

In [ ]:
# stop parameter
stop_loss = 0.1             # 10%
stop_loss_trail = True      # trailing-stop-loss
take_profit = 0.15          # 15%

# generate a portfolio instance with all three types of exits
pf = vbt.Portfolio.from_signals(
    close,                          # price info (defines also the index of any timeline)
    entries,                        # series (boolean) of LONG-entry-signals
    exits,                          # series (boolean) of LONG entry-signals
    short_entries = short_entries,  # series (boolean) of SHORT-entry-signals
    short_exits = short_exits,      # series (boolean) of SHORT-entry-signals
    sl_stop=stop_loss,              # stop loss
    sl_trail=stop_loss_trail,       # trailing stop loss
    tp_stop=take_profit,            # take profit
    init_cash=10_000,               # initial cash
    freq='D',                       # all parameters on daily base
)

In [ ]:
# list of trades with key data, amended by the trade type
trades = classify_exit_types(
    trades=pf.trades.records_readable,
    take_profit=take_profit,
    exits=exits
)

# generating timeline for standard + specific trading parameter
timeline=get_timeline_extended(prices, entries, exits, trades)     # standards (price, entry, exits)
timeline['bb_upper'] = bb_upper
timeline['bb_lower'] = bb_lower
timeline['bb_middle'] = bb_middle

# portfolio
timeline['position'] = np.sign(pf.net_exposure())
timeline['pnl'] = pf.cumulative_returns()
timeline['assets'] = pf.assets()
timeline['cash'] = pf.cash()
timeline['value'] = pf.value()
timeline['gross_exposure'] = pf.gross_exposure()
timeline['net_exposure'] = pf.net_exposure()

We clearly see a different behaviour. The position-curve jumps from 1 (= in Long-position) to 0 (= Flat) to -1 (= in Short-position)

In [ ]:
fig = plot_multi_subplot_trading_data(
    timeline,
    subplot_config_01,
    title = f'Overview for {ticker}, from {start_date} to {end_date}',
    size=(1400, 500),
    theme='plotly',
)
fig.show()

In [ ]:
# Combine trades, PnL, exposure and cash (using built-in subplots)
fig = pf.plots(subplots=['trades','trade_pnl','net_exposure', 'cash'],
               make_subplots_kwargs={'row_heights': [0.7, 0.1, 0.1, 0.1]},
               width=1400, height=800)
fig.show()

When we inspect the trades-record and the timelines, via our `lens_at_entry_exit()` function, we can confirm all the single observations we made so far.

* If we go long -- we use all available cash
* if we go short -- we calculate the number of assets to be sold short by the current value of the portfolio.

So in fact we mimic a behaviour, defined so far by `size_type`= 'Percent' and `size`=1.

In [ ]:
pf.trades.records_readable.head(5)

Exit Trade Id Column  Size Entry Timestamp  Avg Entry Price  Entry Fees  \
0              0   AAPL 65.90      2022-03-11           151.74        0.00   
1              1   AAPL 62.08      2022-03-24           170.71        0.00   
2              2   AAPL 72.21      2022-04-26           153.77        0.00   
3              3   AAPL 78.73      2022-05-09           149.34        0.00   
4              4   AAPL 78.59      2022-05-20           135.13        0.00   

  Exit Timestamp  Avg Exit Price  Exit Fees      PnL  Return Direction  \
0     2022-03-18          160.82       0.00   597.82    0.06      Long   
1     2022-04-11          162.55       0.00   506.54    0.05     Short   
2     2022-05-04          162.82       0.00   652.95    0.06      Long   
3     2022-05-19          134.90       0.00 -1137.38   -0.10      Long   
4     2022-05-27          146.97       0.00   930.08    0.09      Long   

   Status  Position Id  
0  Closed            0  
1  Closed            1  
2  Closed            2  
3  Closed            3  
4  Closed            4

In [ ]:
# timeline around entry and exit of the first trade (LONG)
entry_date = '2022-03-11'
exit_date = '2022-03-18'
n_r = 1             # number of rows before/aftr entry/exit
lense_at_entry_exit(timeline, entry_date, exit_date, n_r)

### Timeline around Entry Date: 2022-03-11 (1 rows before and after)



open   high    low  close  sys_entries  sys_exits  eff_entries  \
Date                                                                          
2022-03-10 157.11 157.29 152.97 155.46        False      False        False   
2022-03-11 155.86 156.21 151.52 151.74         True      False         True   
2022-03-14 148.53 151.15 147.20 147.71        False      False        False   

            eff_exits_system  eff_exits_stop_loss  eff_exits_take_profit  \
Date                                                                       
2022-03-10             False                False                  False   
2022-03-11             False                False                  False   
2022-03-14             False                False                  False   

            bb_upper  bb_lower  bb_middle  position   pnl  assets     cash  \
Date                                                                         
2022-03-10    170.77    153.41     162.09      0.00  0.00    0.00 10000.00   
2022-03-11    170.45    152.03     161.24      1.00  0.00   65.90     0.00   
2022-03-14    171.07    149.64     160.36      1.00 -0.03   65.90     0.00   

              value  gross_exposure  net_exposure  
Date                                               
2022-03-10 10000.00            0.00          0.00  
2022-03-11 10000.00            1.00          1.00  
2022-03-14  9734.37            1.00          1.00



### Timeline around Exit Date: 2022-03-18 (1 rows before and after)



open   high    low  close  sys_entries  sys_exits  eff_entries  \
Date                                                                          
2022-03-17 155.55 157.89 154.59 157.52        False      False        False   
2022-03-18 157.41 161.31 156.68 160.82        False       True        False   
2022-03-21 160.35 163.14 159.86 162.19        False      False        False   

            eff_exits_system  eff_exits_stop_loss  eff_exits_take_profit  \
Date                                                                       
2022-03-17             False                False                  False   
2022-03-18              True                False                  False   
2022-03-21             False                False                  False   

            bb_upper  bb_lower  bb_middle  position  pnl  assets     cash  \
Date                                                                        
2022-03-17    167.43    149.46     158.45      1.00 0.04   65.90     0.00   
2022-03-18    166.65    149.76     158.21      0.00 0.06    0.00 10597.82   
2022-03-21    166.33    149.89     158.11      0.00 0.06    0.00 10597.82   

              value  gross_exposure  net_exposure  
Date                                               
2022-03-17 10380.66            1.00          1.00  
2022-03-18 10597.82            0.00          0.00  
2022-03-21 10597.82            0.00          0.00

In [ ]:
# timeline around entry and exit of the second trade (SHORT)
entry_date = '2022-03-24'
exit_date = '2022-04-11'
n_r = 1             # number of rows before/aftr entry/exit
lense_at_entry_exit(timeline, entry_date, exit_date, n_r)

### Timeline around Entry Date: 2022-03-24 (1 rows before and after)



open   high    low  close  sys_entries  sys_exits  eff_entries  \
Date                                                                          
2022-03-23 164.75 169.31 164.41 166.93        False      False        False   
2022-03-24 167.76 170.78 166.93 170.71        False      False         True   
2022-03-25 170.52 171.90 169.42 171.35        False      False        False   

            eff_exits_system  eff_exits_stop_loss  eff_exits_take_profit  \
Date                                                                       
2022-03-23             False                False                  False   
2022-03-24             False                False                  False   
2022-03-25             False                False                  False   

            bb_upper  bb_lower  bb_middle  position  pnl  assets     cash  \
Date                                                                        
2022-03-23    168.32    149.34     158.83      0.00 0.06    0.00 10597.82   
2022-03-24    170.20    148.57     159.39     -1.00 0.06  -62.08 21195.63   
2022-03-25    171.85    147.89     159.87     -1.00 0.06  -62.08 21195.63   

              value  gross_exposure  net_exposure  
Date                                               
2022-03-23 10597.82            0.00          0.00  
2022-03-24 10597.82            1.00         -1.00  
2022-03-25 10558.24            1.00         -1.00



### Timeline around Exit Date: 2022-04-11 (1 rows before and after)



open   high    low  close  sys_entries  sys_exits  eff_entries  \
Date                                                                          
2022-04-08 168.46 168.46 165.93 166.81        False      False        False   
2022-04-11 165.45 165.77 162.31 162.55        False      False        False   
2022-04-12 164.78 166.59 163.42 164.42        False      False        False   

            eff_exits_system  eff_exits_stop_loss  eff_exits_take_profit  \
Date                                                                       
2022-04-08             False                False                  False   
2022-04-11             False                 True                  False   
2022-04-12             False                False                  False   

            bb_upper  bb_lower  bb_middle  position  pnl  assets     cash  \
Date                                                                        
2022-04-08    181.55    151.10     166.32     -1.00 0.08  -62.08 21195.63   
2022-04-11    179.84    154.29     167.06      0.00 0.11    0.00 11104.36   
2022-04-12    178.56    156.80     167.68      0.00 0.11    0.00 11104.36   

              value  gross_exposure  net_exposure  
Date                                               
2022-04-08 10840.13            1.00         -1.00  
2022-04-11 11104.36            0.00          0.00  
2022-04-12 11104.36            0.00          0.00

Lets go a step further and investigate into the impact of `size_type` and `size` in a LongShort-strategy.

Surprise: If we set `size_type`to 'Percent' and `size`to 0.3 (as in the previous examples), we get a error-message: ValueError: SizeType.Percent does not support position reversal using signals.

The explanation in the Docs is somewhat unsatisfactory. I did not find any substantial rationale for it, so we have to acept it for now. `size_type` set to 'Percent' and `size` different from 1.0  will not work for LongShort-Strategies.

Good news. If we do not specify `size_type`and `size` we always use 100% available cash for Long-Entries and 100% of the current portfolio value for the Short-Entries.   

What works:
* `size_type`= 'Value', trade volume =  `size` money-units.
* `size_type` = 'Amount', trade-volume =`size` number of assets

See the example below:



In [ ]:
# stop parameter
stop_loss = 0.1                     # 10%
stop_loss_trail = True              # trailing-stop-loss
take_profit = 0.15                  # 15%

# generate a portfolio instance with all three types of exits
pf = vbt.Portfolio.from_signals(
    close,                          # price info (defines also the index of any timeline)
    entries,                        # series (boolean) of LONG-entry-signals
    exits,                          # series (boolean) of LONG entry-signals
    short_entries = short_entries,  # series (boolean) of SHORT-entry-signals
    short_exits = short_exits,      # series (boolean) of SHORT-entry-signals
    sl_stop=stop_loss,              # stop loss
    sl_trail=stop_loss_trail,       # trailing stop loss
    tp_stop=take_profit,            # take profit
    size_type ='Amount',            # size_type is number of shares
    size= 80,                       # trade always 80 shares
    init_cash=10_000,               # initial cash
    freq='D',                       # all parameters on daily base
)

# list of trades with key data, amended by the trade type
trades = classify_exit_types(
    trades=pf.trades.records_readable,
    take_profit=take_profit,
    exits=exits
)


In [ ]:
# Combine trades, PnL, exposure, and underwater plots (using built-in subplots)
fig = pf.plots(subplots=['trades','trade_pnl','net_exposure', 'cash'],
               make_subplots_kwargs={'row_heights': [0.7, 0.1, 0.1, 0.1]},
               width=1400, height=600)
fig.show()

In [ ]:
trades.head(10)

Exit Trade Id Column  Size Entry Timestamp  Avg Entry Price  Entry Fees  \
0              0   AAPL 65.90      2022-03-11           151.74        0.00   
1              1   AAPL 80.00      2022-03-24           170.71        0.00   
2              2   AAPL 73.16      2022-04-26           153.77        0.00   
3              3   AAPL 79.76      2022-05-09           149.34        0.00   
4              4   AAPL 79.62      2022-05-20           135.13        0.00   
5              5   AAPL 80.00      2022-06-13           129.52        0.00   
6              6   AAPL 80.00      2022-07-21           152.58        0.00   
7              7   AAPL 72.69      2022-08-30           156.29        0.00   
8              8   AAPL 72.71      2022-10-03           140.10        0.00   
9              9   AAPL 80.00      2022-10-25           149.83        0.00   

  Exit Timestamp  Avg Exit Price  Exit Fees      PnL  Return Direction  \
0     2022-03-18          160.82       0.00   597.82    0.06      Long   
1     2022-04-11          162.55       0.00   652.76    0.05     Short   
2     2022-05-04          162.82       0.00   661.55    0.06      Long   
3     2022-05-19          134.90       0.00 -1152.35   -0.10      Long   
4     2022-05-27          146.97       0.00   942.33    0.09      Long   
5     2022-06-24          139.13       0.00   768.43    0.07      Long   
6     2022-08-10          166.45       0.00 -1109.83   -0.09     Short   
7     2022-09-29          140.13       0.00 -1174.60   -0.10      Long   
8     2022-10-21          144.84       0.00   344.66    0.03      Long   
9     2022-11-02          142.64       0.00   575.15    0.05     Short   

   Status  Position Id  exit_type  
0  Closed            0     system  
1  Closed            1  stop_loss  
2  Closed            2     system  
3  Closed            3  stop_loss  
4  Closed            4     system  
5  Closed            5     system  
6  Closed            6  stop_loss  
7  Closed            7  stop_loss  
8  Closed            8     system  
9  Closed            9  stop_loss

Quite interesting:
* The Sizes of the LongTrade are different, but always smaller or equal to 80.
* The Sizes of the ShortTrades are always 80.

Why is this?
* LongEntry: we may have not enough cash to fill the order for 80 shares. So we order less assets, but consume all the available cash. Therefore the asset number may be less than 80 (but never more than 80). By defailt, we allow a **partial filling of an order**.
* ShortEntry: for short we will do a short selling, i.e. we borrow 80 shares (from somebody outside our portfolio) and sell it. So the order size is always 80 (and not limited by our cash).   




Now lets exclude partial filling. The portfolio instance is as follows:

In [ ]:
# stop parameter
stop_loss = 0.1                     # 10%
stop_loss_trail = True              # trailing-stop-loss
take_profit = 0.15                  # 15%

# generate a portfolio instance with all three types of exits
pf = vbt.Portfolio.from_signals(
    close,                          # price info (defines also the index of any timeline)
    entries,                        # series (boolean) of LONG-entry-signals
    exits,                          # series (boolean) of LONG entry-signals
    short_entries = short_entries,  # series (boolean) of SHORT-entry-signals
    short_exits = short_exits,      # series (boolean) of SHORT-entry-signals
    sl_stop=stop_loss,              # stop loss at 5%
    sl_trail=stop_loss_trail,       # trailing stop loss
    tp_stop=take_profit,            # take profit at 15%
    size_type ='Amount',            # size_type is number of shares
    size= 80,                       # trade always 80 shares
    accumulate=False,
    allow_partial=False,            # allow partial trades
    init_cash=10_000,               # initial cash
    freq='D',                       # all parameters on daily base
)

# list of trades with key data, amended by the trade type
trades = classify_exit_types(
    trades=pf.trades.records_readable,
    take_profit=take_profit,
    exits=exits
)

What do we observe now ?
* ShortTrades: remains unchanged, will be executed for 80 assets per trades
* LongTrades: only these LongTrades are executed, where we have suffcient cash to buy 80 assets, if cash is insufficient the order is dropped.

So all trades are now of size 80.

In [ ]:
trades.head(10)

Exit Trade Id Column  Size Entry Timestamp  Avg Entry Price  Entry Fees  \
0              0   AAPL 80.00      2022-03-24           170.71        0.00   
1              1   AAPL 80.00      2022-06-13           129.52        0.00   
2              2   AAPL 80.00      2022-07-21           152.58        0.00   
3              3   AAPL 80.00      2022-10-25           149.83        0.00   
4              4   AAPL 80.00      2022-12-15           134.47        0.00   
5              5   AAPL 80.00      2023-01-23           139.01        0.00   
6              6   AAPL 80.00      2023-03-20           155.30        0.00   
7              7   AAPL 80.00      2023-04-28           167.41        0.00   
8              8   AAPL 80.00      2023-06-30           191.64        0.00   
9              9   AAPL 80.00      2023-08-30           185.65        0.00   

  Exit Timestamp  Avg Exit Price  Exit Fees      PnL  Return Direction  \
0     2022-04-11          162.55       0.00   652.76    0.05     Short   
1     2022-06-24          139.13       0.00   768.43    0.07      Long   
2     2022-08-10          166.45       0.00 -1109.83   -0.09     Short   
3     2022-11-02          142.64       0.00   575.15    0.05     Short   
4     2023-01-11          131.51       0.00  -237.22   -0.02      Long   
5     2023-02-15          153.26       0.00 -1139.38   -0.10     Short   
6     2023-04-12          157.96       0.00  -213.12   -0.02     Short   
7     2023-06-12          181.59       0.00 -1133.79   -0.08     Short   
8     2023-08-02          190.27       0.00   109.87    0.01     Short   
9     2023-09-07          175.67       0.00   798.60    0.05     Short   

   Status  Position Id  exit_type  
0  Closed            0  stop_loss  
1  Closed            1     system  
2  Closed            2  stop_loss  
3  Closed            3  stop_loss  
4  Closed            4     system  
5  Closed            5  stop_loss  
6  Closed            6  stop_loss  
7  Closed            7  stop_loss  
8  Closed            8  stop_loss  
9  Closed            9  stop_loss

In [ ]:
# Combine trades, PnL, exposure, and underwater plots (using built-in subplots)
fig = pf.plots(subplots=['trades','assets','net_exposure', 'cash'],
               make_subplots_kwargs={'row_heights': [0.7, 0.1, 0.1, 0.1]},
               width=1400, height=600)
fig.show()

Now we plot the detailed sub-plots for more clarification:

In [ ]:
pf.plot_assets(width=1400, height=200).show()

In [ ]:
pf.plot_asset_value(width=1400, height=200).show()

The plot of net_exposure shows an oscillating behaviour, that needs some explanations:
* on the LongSide net_exposure never exceeds 1,
* on the Short-Side, we see different steps up to -3.9.

The behaviour on the long side is easy to explain.
* Our portfolio executes only trades if sufficient cash for exactly 80 shares is available.
* Therefore the asset_value of the entered LongPositions will always be smaller than the available cash at the entry bar (= portfolio value).
* Hence,  net_exposure = (asset_value_Long + asset_value_Short) / value will always be less than 1.

For explaining the behaviour on the short side, we need again to inspect the timelines around the entries/exits.  

In [ ]:
pf.plot_net_exposure(width=1400, height=200).show()

In [ ]:
pf.plot_cash(width=1400, height=200).show()

We can clearly see, that our strategy is not profitable, So the portfolio value is significantly reduced over time.

In [ ]:
pf.plot_value(width=1400, height=400).show()

We generate the timeline and apply the lense on several trades

In [ ]:
# generating timeline for standard + specific trading parameter
timeline=get_timeline_extended(prices, entries, exits, trades)     # standards (price, entry, exits)

# portfolio
timeline['position'] = np.sign(pf.net_exposure())
timeline['pnl'] = pf.cumulative_returns()
timeline['assets'] = pf.assets()
timeline['asset_value'] = pf.asset_value()
timeline['cash'] = pf.cash()
timeline['value'] = pf.value()
timeline['gross_exposure'] = pf.gross_exposure()
timeline['net_exposure'] = pf.net_exposure()

In [ ]:
trades.head(20)

Exit Trade Id Column  Size Entry Timestamp  Avg Entry Price  Entry Fees  \
0               0   AAPL 80.00      2022-03-24           170.71        0.00   
1               1   AAPL 80.00      2022-06-13           129.52        0.00   
2               2   AAPL 80.00      2022-07-21           152.58        0.00   
3               3   AAPL 80.00      2022-10-25           149.83        0.00   
4               4   AAPL 80.00      2022-12-15           134.47        0.00   
5               5   AAPL 80.00      2023-01-23           139.01        0.00   
6               6   AAPL 80.00      2023-03-20           155.30        0.00   
7               7   AAPL 80.00      2023-04-28           167.41        0.00   
8               8   AAPL 80.00      2023-06-30           191.64        0.00   
9               9   AAPL 80.00      2023-08-30           185.65        0.00   
10             10   AAPL 80.00      2023-11-10           184.66        0.00   
11             11   AAPL 80.00      2024-05-03           181.90        0.00   
12             12   AAPL 80.00      2024-06-14           211.06        0.00   
13             13   AAPL 80.00      2024-07-10           231.41        0.00   
14             14   AAPL 80.00      2024-09-30           231.70        0.00   
15             15   AAPL 80.00      2024-10-15           232.54        0.00   
16             16   AAPL 80.00      2024-11-26           234.00        0.00   
17             17   AAPL 80.00      2025-02-14           243.77        0.00   
18             18   AAPL 80.00      2025-07-01           207.38        0.00   
19             19   AAPL 80.00      2025-08-07           219.57        0.00   

   Exit Timestamp  Avg Exit Price  Exit Fees      PnL  Return Direction  \
0      2022-04-11          162.55       0.00   652.76    0.05     Short   
1      2022-06-24          139.13       0.00   768.43    0.07      Long   
2      2022-08-10          166.45       0.00 -1109.83   -0.09     Short   
3      2022-11-02          142.64       0.00   575.15    0.05     Short   
4      2023-01-11          131.51       0.00  -237.22   -0.02      Long   
5      2023-02-15          153.26       0.00 -1139.38   -0.10     Short   
6      2023-04-12          157.96       0.00  -213.12   -0.02     Short   
7      2023-06-12          181.59       0.00 -1133.79   -0.08     Short   
8      2023-08-02          190.27       0.00   109.87    0.01     Short   
9      2023-09-07          175.67       0.00   798.60    0.05     Short   
10     2023-12-22          191.79       0.00  -570.61   -0.04     Short   
11     2024-06-11          205.75       0.00 -1908.51   -0.13     Short   
12     2024-07-09          227.14       0.00 -1286.46   -0.08     Short   
13     2024-07-24          217.07       0.00  1147.41    0.06     Short   
14     2024-10-07          220.45       0.00   899.74    0.05     Short   
15     2024-10-30          228.81       0.00   298.32    0.02     Short   
16     2024-12-26          257.85       0.00 -1908.17   -0.10     Short   
17     2025-02-27          236.49       0.00   582.01    0.03     Short   
18     2025-07-29          210.83       0.00  -275.42   -0.02     Short   
19     2025-09-10          226.57       0.00  -560.21   -0.03     Short   

    Status  Position Id  exit_type  
0   Closed            0  stop_loss  
1   Closed            1     system  
2   Closed            2  stop_loss  
3   Closed            3  stop_loss  
4   Closed            4     system  
5   Closed            5  stop_loss  
6   Closed            6  stop_loss  
7   Closed            7  stop_loss  
8   Closed            8  stop_loss  
9   Closed            9  stop_loss  
10  Closed           10  stop_loss  
11  Closed           11  stop_loss  
12  Closed           12  stop_loss  
13  Closed           13  stop_loss  
14  Closed           14  stop_loss  
15  Closed           15  stop_loss  
16  Closed           16  stop_loss  
17  Closed           17  stop_loss  
18  Closed           18  stop_loss  
19  Closed           19  sto

Lets now look to the Short side. We will inspect the timeline around entries and exits of positions.

The reviwew of the timeline around the first trade (Entry at '2022-03-24') reveals the following:
*  on 2022-03-24 we sell short 80 shares of AAPL at 170.71
*  once sold short, asset value equals (-80 * 170,71) = -13,656.85
*  cash equals 10,000 + 13,656.85 = 23,656.85
*  value equals 10,000 (since asset_price did not change so far)
*  net_exposure = (asset_value_Long + asset_value_Short) / value  -13,656.85 / 10,000 = -1.365

Since we are selling short (means borrowing assets from elsewhere) we are not limited to any cash-restraint of our portfolio. Therefore the asset_value of our short position may exceed the portfolio value (as in our case for the entry bar: asset_value = -13,656.85, Portfolio value = 10,000)





In [ ]:
# timeline around entry and exit of the second trade (SHORT)
entry_date = '2022-03-24'
exit_date = '2022-04-11'
n_r = 1             # number of rows before/aftr entry/exit
lense_at_entry_exit(timeline, entry_date, exit_date, n_r)

### Timeline around Entry Date: 2022-03-24 (1 rows before and after)



open   high    low  close  sys_entries  sys_exits  eff_entries  \
Date                                                                          
2022-03-23 164.75 169.31 164.41 166.93        False      False        False   
2022-03-24 167.76 170.78 166.93 170.71        False      False         True   
2022-03-25 170.52 171.90 169.42 171.35        False      False        False   

            eff_exits_system  eff_exits_stop_loss  eff_exits_take_profit  \
Date                                                                       
2022-03-23             False                False                  False   
2022-03-24             False                False                  False   
2022-03-25             False                False                  False   

            position   pnl  assets  asset_value     cash    value  \
Date                                                                
2022-03-23      0.00  0.00    0.00         0.00 10000.00 10000.00   
2022-03-24     -1.00  0.00  -80.00    -13656.85 23656.85 10000.00   
2022-03-25     -1.00 -0.01  -80.00    -13707.85 23656.85  9949.00   

            gross_exposure  net_exposure  
Date                                      
2022-03-23            0.00          0.00  
2022-03-24            0.79         -1.37  
2022-03-25            0.79         -1.36



### Timeline around Exit Date: 2022-04-11 (1 rows before and after)



open   high    low  close  sys_entries  sys_exits  eff_entries  \
Date                                                                          
2022-04-08 168.46 168.46 165.93 166.81        False      False        False   
2022-04-11 165.45 165.77 162.31 162.55        False      False        False   
2022-04-12 164.78 166.59 163.42 164.42        False      False        False   

            eff_exits_system  eff_exits_stop_loss  eff_exits_take_profit  \
Date                                                                       
2022-04-08             False                False                  False   
2022-04-11             False                 True                  False   
2022-04-12             False                False                  False   

            position  pnl  assets  asset_value     cash    value  \
Date                                                               
2022-04-08     -1.00 0.03  -80.00    -13344.60 23656.85 10312.25   
2022-04-11      0.00 0.07    0.00         0.00 10652.76 10652.76   
2022-04-12      0.00 0.07    0.00         0.00 10652.76 10652.76   

            gross_exposure  net_exposure  
Date                                      
2022-04-08            0.78         -1.38  
2022-04-11            0.00          0.00  
2022-04-12            0.00          0.00

Now lets take deeper dive into the three consecutive trades, starting on 2024-05-03, 2024-06-14 and 2024-07-10. We observe different net_exposure values, ranging down to - 3.87. Why is that?

* net_exposure (in the special case of in a ShortPositionOnly) equals to  asset_values / value.  
* we see a declining portfolio value over time, so in May 2024, the portfolio value shrunk already to 8,500.84 (starting from 10,000) .
* The increased price of AAPL (181.89) results is an increasing value of 80 AAPL-assets
* the net_exposure goes down to -1.711, that is less than the net_exposure of the first trade (= -1.37), due to the increased absolute value of asset-value (nominator) and decreased portfolio-value (denominator).

In [ ]:
# timeline around entry and exit of the second trade (SHORT)
entry_date = '2024-05-03'
exit_date = '2024-06-11'
n_r = 1             # number of rows before/aftr entry/exit
lense_at_entry_exit(timeline, entry_date, exit_date, n_r)

### Timeline around Entry Date: 2024-05-03 (1 rows before and after)



open   high    low  close  sys_entries  sys_exits  eff_entries  \
Date                                                                          
2024-05-02 171.11 172.02 169.51 171.63        False       True        False   
2024-05-03 185.14 185.49 181.18 181.90        False      False         True   
2024-05-06 180.87 182.71 178.96 180.24        False      False        False   

            eff_exits_system  eff_exits_stop_loss  eff_exits_take_profit  \
Date                                                                       
2024-05-02             False                False                  False   
2024-05-03             False                False                  False   
2024-05-06             False                False                  False   

            position   pnl  assets  asset_value     cash   value  \
Date                                                               
2024-05-02      0.00 -0.15    0.00         0.00  8500.85 8500.85   
2024-05-03     -1.00 -0.15  -80.00    -14551.69 23052.55 8500.85   
2024-05-06     -1.00 -0.14  -80.00    -14419.18 23052.55 8633.37   

            gross_exposure  net_exposure  
Date                                      
2024-05-02            0.00          0.00  
2024-05-03            0.71         -1.71  
2024-05-06            0.70         -1.72



### Timeline around Exit Date: 2024-06-11 (1 rows before and after)



open   high    low  close  sys_entries  sys_exits  eff_entries  \
Date                                                                          
2024-06-10 195.57 195.97 190.85 191.82        False      False        False   
2024-06-11 192.34 205.76 192.32 205.75        False      False        False   
2024-06-12 205.97 218.71 205.50 211.63        False      False        False   

            eff_exits_system  eff_exits_stop_loss  eff_exits_take_profit  \
Date                                                                       
2024-06-10             False                False                  False   
2024-06-11             False                 True                  False   
2024-06-12             False                False                  False   

            position   pnl  assets  asset_value     cash   value  \
Date                                                               
2024-06-10     -1.00 -0.23  -80.00    -15345.37 23052.55 7707.17   
2024-06-11      0.00 -0.34    0.00         0.00  6592.34 6592.34   
2024-06-12      0.00 -0.34    0.00         0.00  6592.34 6592.34   

            gross_exposure  net_exposure  
Date                                      
2024-06-10            0.72         -1.65  
2024-06-11            0.00          0.00  
2024-06-12            0.00          0.00

Looking at the next trade (Entry on 2024-06-14) we can observe:
* price of AAPL increased (to 211.05 at entry bar)
* due to the non profitable previous trade, portfolio value has futher decreased (to 6,260.19)  
* in the net_exposure formula we see now higher asset values (due to increased asset price) and lower portfolio value that results in a further reduced net_exposure (-2.561 et the entry bar)

This continues during the next trade (entry on 2024-07-10).
* The AAPL went further up (hence the asset_values of 80 AAPL assets increase),
* the previous trade was not profiteable, hence the portfolio value was futher reduced.

In the end the net_exposure went further down to -3.489 at the entry bar.

This explayins the principal behaviour of the net_exposure for the short sides.

In [ ]:
# timeline around entry and exit of the second trade (SHORT)
entry_date = '2024-06-14'
exit_date = '2024-07-09'
n_r = 1             # number of rows before/aftr entry/exit
lense_at_entry_exit(timeline, entry_date, exit_date, n_r)

### Timeline around Entry Date: 2024-06-14 (1 rows before and after)



open   high    low  close  sys_entries  sys_exits  eff_entries  \
Date                                                                          
2024-06-13 213.29 215.29 210.17 212.79        False      False        False   
2024-06-14 212.41 213.72 209.87 211.06        False      False         True   
2024-06-17 211.93 217.47 211.28 215.21        False      False        False   

            eff_exits_system  eff_exits_stop_loss  eff_exits_take_profit  \
Date                                                                       
2024-06-13             False                False                  False   
2024-06-14             False                False                  False   
2024-06-17             False                False                  False   

            position   pnl  assets  asset_value     cash   value  \
Date                                                               
2024-06-13      0.00 -0.34    0.00         0.00  6592.34 6592.34   
2024-06-14     -1.00 -0.34  -80.00    -16884.52 23476.86 6592.34   
2024-06-17     -1.00 -0.37  -80.00    -17216.67 23476.86 6260.20   

            gross_exposure  net_exposure  
Date                                      
2024-06-13            0.00          0.00  
2024-06-14            0.62         -2.56  
2024-06-17            0.63         -2.49



### Timeline around Exit Date: 2024-07-09 (1 rows before and after)



open   high    low  close  sys_entries  sys_exits  eff_entries  \
Date                                                                          
2024-07-08 225.56 226.31 221.74 226.28        False      False        False   
2024-07-09 226.39 227.85 224.84 227.14        False      False        False   
2024-07-10 227.75 231.51 227.70 231.41        False      False         True   

            eff_exits_system  eff_exits_stop_loss  eff_exits_take_profit  \
Date                                                                       
2024-07-08             False                False                  False   
2024-07-09             False                 True                  False   
2024-07-10             False                False                  False   

            position   pnl  assets  asset_value     cash   value  \
Date                                                               
2024-07-08     -1.00 -0.46  -80.00    -18102.65 23476.86 5374.22   
2024-07-09      0.00 -0.47    0.00         0.00  5305.88 5305.88   
2024-07-10     -1.00 -0.47  -80.00    -18512.66 23818.55 5305.88   

            gross_exposure  net_exposure  
Date                                      
2024-07-08            0.64         -2.32  
2024-07-09            0.00          0.00  
2024-07-10            0.58         -3.49

In [ ]:
# timeline around entry and exit of the second trade (SHORT)
entry_date = '2024-07-10'
exit_date = '2024-07-24'
n_r = 1             # number of rows before/aftr entry/exit
lense_at_entry_exit(timeline, entry_date, exit_date, n_r)

### Timeline around Entry Date: 2024-07-10 (1 rows before and after)



open   high    low  close  sys_entries  sys_exits  eff_entries  \
Date                                                                          
2024-07-09 226.39 227.85 224.84 227.14        False      False        False   
2024-07-10 227.75 231.51 227.70 231.41        False      False         True   
2024-07-11 229.83 230.82 224.25 226.03        False      False        False   

            eff_exits_system  eff_exits_stop_loss  eff_exits_take_profit  \
Date                                                                       
2024-07-09             False                 True                  False   
2024-07-10             False                False                  False   
2024-07-11             False                False                  False   

            position   pnl  assets  asset_value     cash   value  \
Date                                                               
2024-07-09      0.00 -0.47    0.00         0.00  5305.88 5305.88   
2024-07-10     -1.00 -0.47  -80.00    -18512.66 23818.55 5305.88   
2024-07-11     -1.00 -0.43  -80.00    -18082.78 23818.55 5735.76   

            gross_exposure  net_exposure  
Date                                      
2024-07-09            0.00          0.00  
2024-07-10            0.58         -3.49  
2024-07-11            0.58         -3.71



### Timeline around Exit Date: 2024-07-24 (1 rows before and after)



open   high    low  close  sys_entries  sys_exits  eff_entries  \
Date                                                                          
2024-07-23 222.86 225.41 221.18 223.49        False      False        False   
2024-07-24 222.49 223.28 215.67 217.07        False      False        False   
2024-07-25 217.45 219.36 213.17 216.02        False      False        False   

            eff_exits_system  eff_exits_stop_loss  eff_exits_take_profit  \
Date                                                                       
2024-07-23             False                False                  False   
2024-07-24             False                 True                  False   
2024-07-25             False                False                  False   

            position   pnl  assets  asset_value     cash   value  \
Date                                                               
2024-07-23     -1.00 -0.41  -80.00    -17879.36 23818.55 5939.18   
2024-07-24      0.00 -0.35    0.00         0.00  6453.29 6453.29   
2024-07-25      0.00 -0.35    0.00         0.00  6453.29 6453.29   

            gross_exposure  net_exposure  
Date                                      
2024-07-23            0.58         -3.83  
2024-07-24            0.00          0.00  
2024-07-25            0.00          0.00

In [ ]:
start_date = '2022-07-10'
end_date = '2024-07-24'
sliced_timeline = timeline.loc[start_date:end_date]

# date of minimum net_exposure
min_net_exposure_date = sliced_timeline['net_exposure'].idxmin()
print(f"Date of minimum net exposure: {min_net_exposure_date}")

# parameters at date of minimum net_exposure
print(f"Minimum net exposure: {sliced_timeline['net_exposure'].min()}")
print(f"Portfolio value at minimum net exposure date: {sliced_timeline.loc[min_net_exposure_date, 'value']}")
print(f"Asset value at minimum net exposure date: {sliced_timeline.loc[min_net_exposure_date, 'asset_value']}")

Date of minimum net exposure: 2024-07-22 00:00:00
Minimum net exposure: -3.877827022805573
Portfolio value at minimum net exposure date: 6022.61474609375
Asset value at minimum net exposure date: -17795.931396484375
